In [15]:
import pandas as pd


In [23]:
df = pd.read_csv("../data/data_20230225.csv").iloc[:60]
df['time_period'] = pd.to_datetime(df['time_period'])
df.head()

time_period  coal_feed  water_supply  valve_opening  \
0 2025-02-23 01:00:00     170.46        956.26          84.65   
1 2025-02-23 01:00:01     170.20        955.86          84.69   
2 2025-02-23 01:00:02     169.98        955.65          84.69   
3 2025-02-23 01:00:03     169.82        955.15          84.68   
4 2025-02-23 01:00:04     169.79        954.89          84.68   

   main_steam_pressure  intermediate_point_temperature   power  
0                22.46                          382.82  283.85  
1                22.46                          382.81  284.22  
2                22.46                          382.81  283.97  
3                22.46                          382.81  283.97  
4                22.46                          382.81  283.85

In [25]:
import altair as alt

x = df.time_period.values
# x = df.index.values
y1 = df.power.values
y2 = df.valve_opening.values

_d_draw = pd.concat([pd.DataFrame({'x': x, 'value':y1, 'label':'功率'}),pd.DataFrame({'x': x, 'value':y2, 'label':'蒸汽阀开度' })])

# 创建第一个图层，用于'y1'数据
chart_y1 = alt.Chart(_d_draw[_d_draw['label'] == '功率']).mark_line().encode(
    x=alt.X('x', title='时间 (mm:ss)', axis=alt.Axis(format='%M:%S')),
    y=alt.Y('value', title='功率 (MW)', scale=alt.Scale(zero=False)),
    color=alt.Color('label:N', legend=alt.Legend(title='测点', 
                                    orient='right',  # 设置为右侧
                                    direction='vertical',  # 垂直方向
                                    offset=3))
).properties(width=600)

# 创建第二个图层，用于'y2'数据
chart_y2 = alt.Chart(_d_draw[_d_draw['label'] == '蒸汽阀开度']).mark_line().encode(
    x='x',
    y=alt.Y('value', title='蒸汽阀开度 (%)', scale=alt.Scale(zero=False)),
    color=alt.Color('label:N', legend=None)  # 这里我们不需要图例，因为已经由第一个图层添加了
).properties(width=600)

# 将两个图层组合在一起，并确保Y轴是独立的
combined_chart = (chart_y1 + chart_y2).resolve_scale(y='independent').properties(title='功率&蒸汽阀开度')

# 显示图表
# st.altair_chart(combined_chart, use_container_width=True)

combined_chart

alt.LayerChart(...)

In [41]:
import json

d = json.loads("{\n  \"time_period\": \"2025-02-23 01:00:00\",\n  \"coal_feed\": 170.46,\n  \"valve_opening\": 84.65\n}")
for k,v in d.items():
    print(k,v)

time_period 2025-02-23 01:00:00
coal_feed 170.46
valve_opening 84.65


In [44]:
from datetime import datetime

date_str = '2025-02-23 01:00:00'
# 定义日期格式
date_format = '%Y-%m-%d %H:%M:%S'

# 将字符串转换为datetime对象
date_time_obj = datetime.strptime(date_str, date_format)

print(date_time_obj)

2025-02-23 01:00:00


In [4]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import numpy as np
import json
from http_api_helper import history_data_retrieve_api, login_api
from datetime import datetime
from plotly.basedatatypes import BaseFigure

login_data = {
    "username": "ics_data",
    "password": "123456",
}
# ['coal_feed', 'water_supply', 'valve_opening', 'main_steam_pressure', 'intermediate_point_temperature', 'power']
tags = ['coal_feed', 'water_supply', 'valve_opening', 'main_steam_pressure', 'intermediate_point_temperature', 'power']
body = {'endTime': '2023-02-25 05:00:00', 'includeBounds': 'True', 'interval': 1000, 'startTime': '2023-02-25 01:00:00', 'namespace': 'unit01', 'tags': tags}
header = {"token":json.loads(login_api(login_data))["data"]["token"]}
datas = history_data_retrieve_api(header,body).json()


def history_mutli_plot(resp):
    fig = go.Figure()
    pdict = {
            "title":"历史曲线",
            "xaxis": dict(title='时间', domain=[0, min(1, 1 - (len(resp['data'])-2) * 0.08)]),
        }
    for idx, data in enumerate(resp['data']):
        y_label = data['tag']
        # x = [datetime.strptime(d['time'], '%Y-%m-%d %H:%M:%S') for d in data['data']]
        x = [datetime.fromtimestamp(d['time']/1000) for d in data['data']]
        y = [d['qos'] for d in data['data']]
        fig.add_trace(go.Scatter(x=x, y=y, name=y_label,yaxis=f'y{idx+1}'))
        if idx==0:
            pdict["yaxis"] = dict( title=y_label, titlefont=dict(color="#1f77b4"), tickfont=dict(color="#1f77b4"),automargin=True)
        else:
            pdict[f"yaxis{idx+1 if idx!=0 else ''}"] = dict( title=y_label, titlefont=dict(color="#1f77b4"), tickfont=dict(color="#1f77b4"), anchor="free", overlaying="y", side="right", position=1-max(0, idx-1)*0.08,automargin=True)
        
    fig.update_layout(**pdict)
    return fig

history_mutli_plot(datas).show()


In [117]:
datetime.fromtimestamp(1677258001000 / 1000.0)

datetime.datetime(2023, 2, 25, 1, 0, 1)

In [7]:
import plotly.graph_objs as go
import numpy as np

x = np.linspace(0, 10, 100)
y1 = np.sin(x)
y2 = np.cos(x)
y3 = x**2
y4 = np.log(x + 1)
y5 = np.exp(x / 2) - 1
y6 = np.tan(x / 2)

fig = go.Figure()

fig.add_trace(go.Scatter(x=x, y=y1, name="Sin(x)", line_color="#1f77b4", yaxis="y1"))
fig.add_trace(go.Scatter(x=x, y=y2, name="Cos(x)", line_color="#ff7f0e", yaxis="y2"))
# fig.add_trace(go.Scatter(x=x, y=y3, name="x^2", yaxis="y3"))
# fig.add_trace(go.Scatter(x=x, y=y4, name="Log(x+1)", yaxis="y4"))
# fig.add_trace(go.Scatter(x=x, y=y5, name="e^(x/2)-1", yaxis="y5"))
# fig.add_trace(go.Scatter(x=x, y=y6, name="Tan(x/2)", yaxis="y6"))

fig.update_layout(
    title="6 Lines with Separate Y-Axes",
    xaxis_title="X Axis",
    yaxis=dict(
        title="Y1 Axis",
        titlefont=dict(color="#1f77b4"),
        tickfont=dict(color="#1f77b4"),
        title_standoff=5,  # 减小标题与轴的距离
        automargin=True     # 减小刻度标签与轴的距离
    ),
    yaxis2=dict(
        title="Y2 Axis",
        titlefont=dict(color="#ff7f0e"),
        tickfont=dict(color="#ff7f0e"),
        anchor="free",
        overlaying="y",
        side="left",
        position=0.9,
        title_standoff=5,
        automargin=True
    )
   
)

fig.show()

In [139]:
N = 100
random_x = np.linspace(0, 1, N)
random_y0 = np.random.randn(N) + 5
random_y1 = np.random.randn(N)
random_y2 = np.random.randn(N) - 5

# Create figure with secondary y-axis 
fig = go.Figure()

# Add traces on the primary y-axis
fig.add_trace(go.Scatter(x=random_x, y=random_y0,
                        mode='lines',
                        name='lines',
                        yaxis='y1'))  # Specify the default y-axis

# Add traces on the secondary y-axis
fig.add_trace(go.Scatter(x=random_x, y=random_y1,
                        mode='lines+markers',
                        name='lines+markers',
                        yaxis='y2'))  # Use the secondary y-axis

# Add traces on the tertiary y-axis
fig.add_trace(go.Scatter(x=random_x, y=random_y2,
                        mode='markers',
                        name='markers',
                        yaxis='y3'))  # Use the tertiary y-axis

# Define layout for secondary and tertiary y-axes
fig.update_layout(
    yaxis=dict(title='Primary Y-axis'),
    yaxis1=dict(title='Secondary Y-axis', overlaying='y', side='right', anchor='free', position=0.95,automargin=True),
    # yaxis2=dict(title='Secondary Y-axis', overlaying='y', side='right', anchor='free', position=0.90,automargin=True),
    yaxis2=dict(title='Tertiary Y-axis', overlaying='y', side='right', anchor='free', position=1, automargin=True),
    xaxis=dict(title='X-axis', domain=[0.01, 0.90]),
    # width=1500, 
    # height=600
)

fig.show()

In [114]:
import plotly.graph_objs as go
import numpy as np

# 假设x轴数据为0到10的等差数列
x = np.linspace(0, 10, 100)

# 生成6组不同的y轴数据，这里为了演示简单，使用了不同函数生成数据
y1 = np.sin(x)
y2 = np.cos(x)
y3 = x**2
y4 = np.log(x + 1)  # 注意对数函数中x+1避免log(0)的情况
y5 = np.exp(x / 2) - 1
y6 = np.tan(x / 2)

# 创建Plotly的Figure对象
fig = go.Figure()

# 添加每条折线到图表中，并分别为它们指定不同的y轴
fig.add_trace(go.Scatter(x=x, y=y1, name="Sin(x)", yaxis="y1"))
fig.add_trace(go.Scatter(x=x, y=y2, name="Cos(x)", yaxis="y2"))
fig.add_trace(go.Scatter(x=x, y=y3, name="x^2", yaxis="y3"))
fig.add_trace(go.Scatter(x=x, y=y4, name="Log(x+1)", yaxis="y4"))
fig.add_trace(go.Scatter(x=x, y=y5, name="e^(x/2)-1", yaxis="y5"))
fig.add_trace(go.Scatter(x=x, y=y6, name="Tan(x/2)", yaxis="y6"))

pdict ={ 
    "title":"6 Lines with Separate Y-Axes",
    "xaxis_title":"X Axis",
    "yaxis": dict(
        title="Y1 Axis",
        titlefont=dict(color="#1f77b4"),
        tickfont=dict(color="#1f77b4")
    ),
    "yaxis2": dict(
        title="Y2 Axis",
        titlefont=dict(color="#ff7f0e"),
        tickfont=dict(color="#ff7f0e"),
        anchor="free",
        overlaying="y",
        side="left",
        position=0.9
    ),
    "yaxis3": dict(
        title="Y3 Axis",
        titlefont=dict(color="#2ca02c"),
        tickfont=dict(color="#2ca02c"),
        anchor="x",
        overlaying="y",
        side="right"
    ),
    "yaxis4": dict(
        title="Y4 Axis",
        titlefont=dict(color="#d62728"),
        tickfont=dict(color="#d62728"),
        anchor="free",
        overlaying="y",
        side="right",
        position=0.95
    ),
    "yaxis5": dict(
        title="Y5 Axis",
        titlefont=dict(color="#9467bd"),
        tickfont=dict(color="#9467bd"),
        anchor="free",
        overlaying="y",
        side="right",
        position=0.8
    ),
    "yaxis6": dict(
        title="Y6 Axis",
        titlefont=dict(color="#e377c2"),
        tickfont=dict(color="#e377c2"),
        anchor="free",
        overlaying="y",
        side="right",
        position=0.65
    )}
# 配置每个y轴的属性
fig.update_layout(**pdict
)

# 显示图表
fig.show()